# Vergrijzing: de ineenstorting van de economie
### Github: https://github.com/0xKobalt/infovis | Github Pages: https://0xkobalt.github.io/infovis/docs/notebook.html

## Introductie
Een vergrijzende bevolking kan een probleem vormen voor de maatschappij. Vergrijzing houdt in dat de gemiddelde leeftijd stijgt en dat er meer ouderen/niet-werkende zijn dan werkenden. Dit komt doordat er beter zorg is voor ouderen en dat er minder kinderen worden geboren.

Vergrijzing heeft invloed op de arbeidsmarkt, belastinginkomsten, zorgkosten en dus de economie.

##### Perspectief 1:
Vergrijzing is een probleem dat verandering in de samenleving vereist, anders stort de economie in. Doordat het aantal niet-werkende stijgt en het aantal werkende krimpt, zou de economie hard getroffen kunnen worden, doordat er minder minder mensen zijn om de kosten, zoals sociale voorzieningen, pensioenen en zorgkosten, te betalen. Verder krimpt de arbeidsmarkt ook, wat economische groei kan beperken. Er zou dus een verandering in de maatschappij moeten komen om dit probleem op te lossen.

##### Perspectief 2:
Vergrijzing is vooral een probleem op regionaal niveau. Doordat jonge mensen naar de grote stad gaan zal de rest van Nederland minder economische groei ervaren. Dit komt doordat de grote steden meer kansen bieden dan het platteland. De arbeidsmarkt en consumentenmarkt zal dus in die regio's krimpen. Waardoor de economische groei stagneerd en daalt.


## Dataset en preprocessing

In [32]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import json
from ipywidgets import interact, IntSlider

In [29]:
bevolking = pd.read_csv("Bevolking_op_1_januari_en_gemiddeld__geslacht__leeftijd_en_regio_22062023_182818.csv", sep=';')
grijzedruk = pd.read_csv('grijs.csv', sep=';')
zorgkosten = pd.read_csv('zorgkosten.csv', sep=';')
uitkeringen = pd.read_csv('Uitkeringen_draft.csv', sep=";")
Provinciale_regionalegroei = pd.read_csv('Provinciale_regionalegroei_draft.csv', sep=';')
Regionale_grijzedruk = pd.read_csv('Corop_grijzedruk_2019.csv', sep=';')
Regionale_economischegroei = pd.read_csv('Corop_economischegroei_2019.csv', sep=";")
levensverwachting = pd.read_csv("Levensverwachting.csv", sep=';',decimal=',')

bevolking = bevolking[bevolking['Leeftijd'] != 'Totaal']
bevolking = bevolking[bevolking["Leeftijd"].str.contains("jaar of ouder") == False]

uitkeringen = uitkeringen.drop(columns=["ID"])

Provinciale_regionalegroei = Provinciale_regionalegroei.drop(columns=["ID"])

result = pd.concat([bevolking, grijzedruk,zorgkosten,uitkeringen, Provinciale_regionalegroei,Regionale_grijzedruk,Regionale_economischegroei,levensverwachting], ignore_index=True, sort=False)

result['RegioS'] = result['RegioS'].str.strip()
result['Perioden'] = result['Perioden'].str[:4]
result['Jaar']=result['Jaar'].str[:4]
result['SocialeUitkeringen_1'] = result['SocialeUitkeringen_1']/1000

Om de opgeschoonde dataset te vormen, hebben we 8 dataset bestanden van het CBS gebruikt. De datasets van het CBS kunnen op de site al op onderwerp (variabelen) , regio en perioden selecteerd worden. De variabelen die we gebruiken zijn, type uitkering en besteding aan dat type tussen 1995 tot en met 2021, procent grijze druk per gemeente in 2020 en verandering van bbp per provincie tussen 1995 tot en met 2021, bevolkingsopbouw en zorgkosten voor 80-plussers. De datasets worden opgeschoond door de volgende operaties, puntkomma's vervangen door komma's, alle spaties verwijderen en de variable van jaar veranderen (bijv. "2010JJ00" veranderen naar "2010"). Bij levenverwachting worden de komma's van de getallen vervangen door punten. De verschillende datasets worden dan samengevoegd om één dataframe te vormen.

## Reflectie

## Work distribution

Perspectief 1:

In [30]:
bevolking = bevolking[bevolking['Leeftijd'] != '95 jaar of ouder']
bevolking = bevolking[bevolking['Leeftijd'] != '105 jaar of ouder']

bevolking_mannen = bevolking[['Perioden', 'Leeftijd', 'Mannen']]
bevolking_vrouwen = bevolking[['Perioden', 'Leeftijd', 'Vrouwen']]

bevolking_mannen = bevolking_mannen[bevolking_mannen['Mannen'] != '.']
bevolking_mannen = bevolking_mannen[bevolking_mannen['Leeftijd'] != 'Totaal']
bevolking_mannen['Mannen'] = pd.to_numeric(bevolking_mannen['Mannen'])

bevolking_vrouwen = bevolking_vrouwen[bevolking_vrouwen['Vrouwen'] != '.']
bevolking_vrouwen = bevolking_vrouwen[bevolking_vrouwen['Leeftijd'] != 'Totaal']
bevolking_vrouwen['Vrouwen'] = pd.to_numeric(bevolking_vrouwen['Vrouwen'])
bevolking_mannen['Mannen'] = -bevolking_mannen['Mannen']

beschikbare_jaren = bevolking['Perioden'].unique()

fig = go.Figure()
fig.add_trace(go.Bar(y=[], x=[], orientation='h', name='Mannen'))
fig.add_trace(go.Bar(y=[], x=[], orientation='h', name='Vrouwen'))
fig.update_layout(barmode='overlay', title_text='', xaxis_title='Bevolkingsaantal', yaxis_title='Leeftijd')

def update_piramide(jaar):
    bevolking_jaar_mannen = bevolking_mannen[bevolking_mannen['Perioden'] == jaar]
    bevolking_jaar_vrouwen = bevolking_vrouwen[bevolking_vrouwen['Perioden'] == jaar]
    
    fig.data[0].y = bevolking_jaar_mannen['Leeftijd']
    fig.data[0].x = bevolking_jaar_mannen['Mannen']
    
    fig.data[1].y = bevolking_jaar_vrouwen['Leeftijd']
    fig.data[1].x = bevolking_jaar_vrouwen['Vrouwen']
    
    fig.update_layout(title_text=f'Bevolkingspiramide {jaar}')
    fig.show()

@interact(jaar=IntSlider(min=min(beschikbare_jaren), max=max(beschikbare_jaren), step=1, value=min(beschikbare_jaren)))
def animate(jaar):
    update_piramide(jaar)

Widget Javascript not detected.  It may not be installed or enabled properly. Reconnecting the current kernel may help.


* Er is dus een kleinere groep mensen die later de zorg van een grote groep ouderen betalen.

Er is een grote groep mensen die tussen de 40 en de 65. De groep tussen 0 en 20 is kleiner. Deze kleinere groep moet de grotere groep over 20 jaar vervangen.

In [16]:
Totaal = go.Scatter(
    x=levensverwachting['Jaar'], 
    y=levensverwachting['Totaal mannen en vrouwen'],
    mode='lines',
    name='Totaal mannen en vrouwen'
)

Mannen = go.Scatter(
    x=levensverwachting['Jaar'], 
    y=levensverwachting['Mannen'],
    mode='lines',
    name='Mannen'
)

Vrouwen = go.Scatter(
    x=levensverwachting['Jaar'], 
    y=levensverwachting['Vrouwen'],
    mode='lines',
    name='Vrouwen'
)

layout = go.Layout(
    title='Levensverwachting in Nederland',
    xaxis=dict(title='Fig. 2. De levensverwachting van mannen en vrouwen tussen 1950 tot en met 2022'),
    yaxis=dict(title='Levensverwachting (jaren)'),
    hovermode='x unified'
)

fig = go.Figure(data=[Totaal, Mannen, Vrouwen], layout=layout)

fig.show()

* Doordat de levensverwachting stijgt zal de groep van ouderen nog groter worden.

Sinds 1972 stijgt de levensverwachting bijna elk jaar. In combinatie met de vorige grafiek is te zien dat de groep van ouderen in de toekomst erg groot zal zijn.

In [17]:
grijzedruk['RegioS']=grijzedruk['RegioS'].str[:4]
grijzedruk['Jaar']=grijzedruk['Jaar'].str[:4]
grijzedruk['Grijze Druk']=grijzedruk['Grijze Druk']/100

grijzedruk = grijzedruk[grijzedruk['RegioS'].isin(['NL01'])]

fig = px.line(
    grijzedruk, 
    x=grijzedruk['Jaar'], 
    y=grijzedruk['Grijze Druk'],
    height=500,
    )


fig.update_yaxes(
    tickformat=',.0%',
)

fig.update_layout(
    title="Grijze druk",
    xaxis_title="Fig. 3: de grijze druk in Nederland van 1995 tot en met 2023")
fig.show()

* De groep werkende krimpt moet steeds een groter groep oudere onderhouden.

Sinds 1995 stijgt de grijze druk. Dat betekent dat het verschil in grootte tussen de groep niet-werkenden en werkenden steeds groter wordt.

In [18]:
zorgkosten['Jaar']=zorgkosten['Jaar'].str[:4]

fig = px.line(
    zorgkosten,
    x=zorgkosten['Jaar'], 
    y=zorgkosten['80-plussers'],
    height=500,
    labels={"x":"Jaar", "y":"Aantal"},
    )

fig.update_layout(
    title="Aantal 80-plussers Wlz/AWBZ-gefinancierde zorg",
    xaxis_title="Fig. 4: Het aantal 80-plussers in de Wlz/AWBZ-gefinancierde zorg",
    yaxis_title="Aantal")
fig.show()

* De zorg voor ouderen wordt steeds duurder.

Sinds 2001 stijgt het aantal ouderen dat zorg ontvangt, gefinancieerd door Wiz/AMBZ.

In [19]:
totaal =  ['T001397']
totaal = result[result['Uitkeringen'].isin(totaal)]

aow = ['A045116']
aow = result[result['Uitkeringen'].isin(aow)]

ouderen =  ['A045119', 'A045137', 'A045121']
ouderen = result[result['Uitkeringen'].isin(ouderen)]

zorgwetten=ouderen.groupby('Perioden')['SocialeUitkeringen_1'].sum()
zorgwetten=zorgwetten.reset_index()

selected_data = totaal.loc[totaal['Uitkeringen'] == 'T001397']
fig = go.Figure()
fig.add_trace(go.Scatter(x=selected_data['Perioden'], y=selected_data['SocialeUitkeringen_1'], mode='lines', fill='tonexty',stackgroup='one', name="Totale uitkeringen"))
fig.add_trace(go.Scatter(x=aow['Perioden'], y=aow['SocialeUitkeringen_1'], mode='lines', fill='tonexty',stackgroup='two', name="Pensioen"))
fig.add_trace(go.Scatter(x=zorgwetten['Perioden'], y=zorgwetten['SocialeUitkeringen_1'], mode='lines', fill='tonexty',  stackgroup='two', name="Zorgwetten"))

fig.update_layout(
    title="Besteding aan uitkeringen",
    yaxis_title="Uitkering (Miljard)",
    xaxis_title="Fig. 5. De verhouding tussen de uitkering die ouderen krijgen en de hoeveelheid")
fig.show()

* Er gaat steeds meer geld naar de ouderen.

Door zorgenwetten wordt het aandeel van uitkeringen dat naar ouderen gaat steeds groter.

Perspectief 2:

In [20]:
corop = json.load(open('coropgebied_gegeneraliseerd_2021.geojson', 'r'))
for feature in corop['features']:
  feature['id'] = feature['properties']['statcode']
fig = px.choropleth(result, locations='RegioS', geojson=corop, color='GrijzeDruk_24')
fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(
    title="Regionale grijze druk",
annotations = [dict(xref='paper',
                                        yref='paper',
                                        x=0.5, y=-0.2,
                                        showarrow=False,
                                        text ='Fig. 6. De percentage grijze druk per gemeente in 2019.')])
fig.show()

* Er is meer grijze druk in de randen van Nederland.

De grijze druk is hoger in het zuiden van Zeeland dan in de regio van Amsterdam.

In [21]:
fig2 = px.choropleth(result, locations='RegioS', geojson=corop, color='BbpVolumemutaties_3')
fig2.update_geos(fitbounds="locations", visible=False)
fig2.update_layout(
    title="Regionale economische groei",
annotations = [dict(xref='paper',
                                        yref='paper',
                                        x=0.5, y=-0.2,
                                        showarrow=False,
                                        text ='Fig. 7. De percentage grijze druk per gemeente in 2019.')])
fig2.show()

* De regionale grijze druk beïnvloed de regionale economische groei.

Het zuiden heeft een lagere economische groei dan de regio van Amsterdam. In combinatie met de vorige grafiek is te zien dat de tint van deze verschillen.

In [22]:
randstad_provincies =  ['PV26', 'PV27', 'PV28']
randstad_provincies = result[result['RegioS'].isin(randstad_provincies)]

de_rest = ['PV20', 'PV21', 'PV22', 'PV23', 'PV25', 'PV29', 'PV31']
de_rest = result[result['RegioS'].isin(de_rest)]

randstad_provincies=randstad_provincies.groupby('Perioden')['BbpVolumemutaties_3'].mean()
randstad_provincies=randstad_provincies.reset_index()

de_rest=de_rest.groupby('Perioden')['BbpVolumemutaties_3'].mean()
de_rest=de_rest.reset_index()

fig = go.Figure()
fig.add_trace(go.Scatter(x=randstad_provincies['Perioden'], y=randstad_provincies['BbpVolumemutaties_3'], mode='lines', name="randstad"))
fig.add_trace(go.Scatter(x=de_rest['Perioden'], y=de_rest['BbpVolumemutaties_3'], mode='lines', name="de rest"))

fig.update_layout(
    title="Verandering van bbp",
    xaxis_title="Fig. 8. De verandering van bbp in percentage van de randstad en de test van Nederland ten opzichte van het jaar daarvoor.")
fig.show()

* De randstad heeft minder last van grijze druk dan de rest van Nederland.

In de grafiek van regionale vergrijzing is te zien dat de randstand minder vergrijzing ervaart dan de rest van Nederland. In deze grafiek is te zien dat (zonder te kijken naar 2008-2009 (Kredietcrisis) en 2019-2021 (COVID-19)) er tussen 2012 en 2019 de economische groei van de randstad hoger is dan van de rest van Nederland.

In [23]:
randstad_provincies =  ['PV26', 'PV27', 'PV28']
randstad_provincies = result[result['RegioS'].isin(randstad_provincies)]

de_rest = ['PV20', 'PV21', 'PV22', 'PV23', 'PV25', 'PV29', 'PV31']
de_rest = result[result['RegioS'].isin(de_rest)]

randstad_provincies=randstad_provincies.groupby('Perioden')['BbpVolumemutaties_3'].mean()
randstad_provincies=randstad_provincies.reset_index()

de_rest=de_rest.groupby('Perioden')['BbpVolumemutaties_3'].mean()
de_rest=de_rest.reset_index()

fig = go.Figure()
fig.add_trace(go.Scatter(x=randstad_provincies['Perioden'], y=randstad_provincies['BbpVolumemutaties_3'], mode='lines', name="randstad"))
fig.add_trace(go.Scatter(x=de_rest['Perioden'], y=de_rest['BbpVolumemutaties_3'], mode='lines', name="de rest"))

fig.update_layout(
    title="Verandering van bbp",
    xaxis_title="Fig. 8. De verandering van bbp in percentage van de randstad en de test van Nederland ten opzichte van het jaar daarvoor.")
fig.show()